In [1]:
# !pip install torchtext==0.6.0

# from torchtext.data.metrics import bleu_score
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.tensorboard import SummaryWriter
from torchtext.data import Field, BucketIterator, TabularDataset, Dataset, Example
import pandas as pd
import numpy as np
import nltk

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)
# device = 'cpu'

cuda


In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install pyvi
from pyvi import ViTokenizer


In [3]:
import sys
import csv
csv.field_size_limit(9999999)

src = Field(sequential=True, 
            use_vocab=True,
            # tokenize = ViTokenizer.tokenize,
            init_token='<sos>',
            eos_token = '<eos>',
            lower = True)

trg = Field(sequential=True, 
            use_vocab=True,
            # tokenize = ViTokenizer.tokenize,
            init_token='<sos>',
            eos_token = '<eos>',
            lower = True)

fields = {'content': ('src', src), 'summary': ('trg', trg)}

train_dataset = TabularDataset('/content/drive/MyDrive/DS_data/zing_news_processed.csv', format='csv', fields=fields)
test_dataset = TabularDataset('/content/drive/MyDrive/DS_data/dantri_processed.csv', format='csv', fields=fields)

In [4]:
src.build_vocab(train_dataset, min_freq=5)

trg.build_vocab(train_dataset, min_freq=5)

print(len(src.vocab))
print(len(trg.vocab))
print(src.vocab.itos)

52080
10374
['<unk>', '<pad>', '<sos>', '<eos>', 'và', 'của', 'là', 'trong', 'các', 'có', 'được', 'cho', 'với', 'người', 'không', 'những', 'đã', 'một', 'khi', 'để', 'này', 'đến', 'ở', 'về', 'đó', 'ông', 'nhiều', 'năm', 'từ', 'cũng', 'trên', 'tại', 'vào', 'sẽ', 'ra', 'tôi', 'sau', 'như', 'theo', 'hơn', 'phải', 'ngày', 'lại', 'còn', 'nhưng', 'bị', 'việc', 'anh', '2', 'biết', 'trước', 'nhà', 'chỉ', 'có_thể', 'làm', 'sự', 'đi', 'đang', 'nhất', 'mình', 'mới', 'nói', '3', 'đây', 'việt_nam', 'cùng', '1', 'tháng', 'mà', 'vẫn', 'họ', 'đồng', 'rất', 'khác', 'hai', 'bộ', 'qua', 'lên', 'cô', 'tới', 'nước', 'hay', 'rằng', '5', 'xe', 'bạn', 'cao', 'cả', 'vì', 'lớn', '4', 'nên', 'do', 'triệu', 'chưa', 'tuổi', '10', 'thì', 'con', 'mỹ', 'lần', 'thấy', 'số', 'điều', 'hàng', 'tp', 'nếu', 'bà', 'từng', 'thời_gian', 'tỉnh', 'cần', 'tuy_nhiên', 'đưa', 'cách', 'gần', 'khiến', 'công_ty', 'bên', '6', 'đầu', '000', 'đường', 'nhận', 'thứ', 'đều', '7', '8', 'tiền', 'tỷ', 'giá', 'bằng', 'mang', 'sử_dụng', 'thêm', 

In [5]:

class Transformer(nn.Module):
    def __init__(
        self,
        embedding_size,
        src_vocab_size,
        trg_vocab_size,
        src_pad_idx,
        num_heads,
        num_encoder_layers,
        num_decoder_layers,
        forward_expansion,
        dropout,
        max_src_len,
        max_trg_len
    ):
        super(Transformer, self).__init__()
        self.max_src_len = max_src_len
        self.max_trg_len = max_trg_len
        self.src_word_embedding = nn.Embedding(src_vocab_size, embedding_size)
        self.src_position_embedding = nn.Embedding(max_src_len, embedding_size)
        self.trg_word_embedding = nn.Embedding(trg_vocab_size, embedding_size)
        self.trg_position_embedding = nn.Embedding(max_trg_len, embedding_size)

        self.transformer = nn.Transformer(
            embedding_size,
            num_heads,
            num_encoder_layers,
            num_decoder_layers,
            forward_expansion,
            dropout,
        )
        self.fc_out = nn.Linear(embedding_size, trg_vocab_size)
        self.dropout = nn.Dropout(dropout)
        self.src_pad_idx = src_pad_idx

    def make_src_mask(self, src):
        src_mask = src.transpose(0, 1) == self.src_pad_idx

        # (N, src_len)
        return src_mask.to(device)

    def forward(self, src, trg):
        if src.shape[0] > self.max_src_len:
            src = src[:self.max_src_len, :]

        if trg.shape[0] > self.max_trg_len:
            trg = trg[:self.max_trg_len, :]

        src_seq_length, N = src.shape
        trg_seq_length, N = trg.shape

        src_positions = (
            torch.arange(0, src_seq_length)
            .unsqueeze(1)
            .expand(src_seq_length, N)
            .to(device)
        )

        trg_positions = (
            torch.arange(0, trg_seq_length)
            .unsqueeze(1)
            .expand(trg_seq_length, N)
            .to(device)
        )

        embed_src = self.dropout(
            (self.src_word_embedding(src) + self.src_position_embedding(src_positions))
        )
        embed_trg = self.dropout(
            (self.trg_word_embedding(trg) + self.trg_position_embedding(trg_positions))
        )

        src_padding_mask = self.make_src_mask(src)
        trg_mask = self.transformer.generate_square_subsequent_mask(trg_seq_length).to(
            device
        )

        out = self.transformer(
            embed_src,
            embed_trg,
            src_key_padding_mask=src_padding_mask,
            tgt_mask=trg_mask,
        )
        out = self.fc_out(out)
        return out

In [6]:
pad_idx = src.vocab.stoi["<pad>"]
import time

def train(model, train_dataset, num_epochs=100, lr=0.001, batch_size=32):

    optimizer = optim.Adam(model.parameters(), lr=lr)
    criterion = nn.CrossEntropyLoss(ignore_index=pad_idx)
    train_iterator = BucketIterator(train_dataset, batch_size=batch_size, device=device, shuffle=True)
    for epoch in range(num_epochs):
        print(f"[Epoch {epoch} / {num_epochs}]")
        model.train()
        losses = []
        c0 = time.time()
        for batch_idx, batch in enumerate(train_iterator):
            # Get input and targets and get to cuda
            inp_data = batch.src.to(device)
            target = batch.trg.to(device)
            output = model(inp_data, target[:-1, :])

            # Output is of shape (trg_len, batch_size, output_dim) but Cross Entropy Loss
            # doesn't take input in that form. For example if we have MNIST we want to have
            # output to be: (N, 10) and targets just (N). Here we can view it in a similar
            # way that we have output_words * batch_size that we want to send in into
            # our cost function, so we need to do some reshapin.
            # Let's also remove the start token while we're at it
            output = output.reshape(-1, output.shape[2])
            target = target[1:].reshape(-1)

            optimizer.zero_grad()

            loss = criterion(output, target)
            losses.append(loss.item())

            # Back prop
            loss.backward()

            # Gradient descent step
            optimizer.step()

        c1 = time.time()
        mean_loss = sum(losses) / len(losses)
        print('loss {}, time {}s'.format(mean_loss, c1-c0))
        torch.save(model.state_dict(),'/content/drive/MyDrive/DS_data/summary_model.pt')

def eval_instance(model, inp, target):
    model.eval()
    src_tensor = inp.split()
    src_tensor.insert(0, src.init_token)
    src_tensor.append(src.eos_token)
    src_tensor = [src.vocab.stoi[i] for i in src_tensor]
    src_tensor = torch.LongTensor(src_tensor).unsqueeze(1).to(device)
    outputs = [trg.vocab.stoi["<sos>"]]
    for i in range(100):
        translate_tensor = torch.LongTensor(outputs).unsqueeze(1).to(device)
        with torch.no_grad():
            output = model(src_tensor, translate_tensor)
        
        best_guess = output.argmax(2)[-1:].item()
        outputs.append(best_guess)

        if best_guess == trg.vocab.stoi["<eos>"]:
            break

    outputs = outputs[1:-1]
    outputs = [trg.vocab.itos[idx] for idx in outputs]
    bleu_score = nltk.translate.bleu_score.sentence_bleu([target.split(' ')], outputs, weights=(0.5, 0.5))
    return ' '.join(outputs), bleu_score

In [7]:
model = Transformer(
    embedding_size=128,
    src_vocab_size=len(src.vocab),
    trg_vocab_size=len(trg.vocab),
    src_pad_idx=src.vocab.stoi["<pad>"],
    num_heads=4,
    num_encoder_layers=1,
    num_decoder_layers=1,
    forward_expansion=2,
    dropout=0.1,
    max_src_len=1000,
    max_trg_len=1000,
).to(device)

model.load_state_dict(torch.load('/content/drive/MyDrive/DS_data/summary_model.pt'))


<All keys matched successfully>

In [ ]:
for example in test_dataset.examples:
  # try:
    if len(str(example.src)) <= 2 or len(str(list(example.trg))) <= 2:
      print(example.src)
      print(example.trg)
  

In [ ]:
total_score = 0
for example in test_dataset.examples:
    inp = ' '.join(example.src)
    target = ' '.join(example.trg)
    if len(str(inp)) < 100 or len(str(target)) < 100:
        print(inp)
        print(target)
        continue
    output, bleu_score = eval_instance(model, inp, target)
    total_score += bleu_score

total_score = total_score/len(test_dataset.examples)
print(total_score)

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


bộ_trưởng đào_ngọc_dung chỉ_tiêu niềm tin về an_sinh xã_hội tăng cao chỉ_tiêu về niềm tin của nhân_dân đánh_giá về an_sinh xã_hội hiện đứng thứ 3 trong hơn 30 chỉ_tiêu niềm tin đó tăng từ 55 lên 68 vào tháng 9 2020 vừa_qua bộ_trưởng bộ lđ tb xh đào_ngọc_dung phát_biểu tại đại_hội thi_đua yêu nước lần thứ 5 của ngành lao_động thương_binh và xã_hội năm 2020 sáng 17 11 tại hà_nội khẳng_định về sự chỉ_đạo quan_tâm sát_sao của đảng nhà_nước trong suốt chặng đường 75 năm nhất_là trong 5 năm qua bộ_trưởng đào_ngọc_dung cho rằng đó là động_lực và niềm tin để toàn ngành nỗ_lực vươn lên phấn_đấu và hoàn_thành tốt các nhiệm_vụ được giao đồng_thời bộ_trưởng cũng gửi lời cảm_ơn và chúc_mừng tới các cán_bộ công_chức viên_chức người lao_động trong ngành đã nỗ_lực để có những kết_quả hôm_nay bộ_trưởng khẳng_định những đóng_góp của mỗi cán_bộ công_chức viên_chức và người lao_động trên từng vị_trí công_tác được ghi_nhận và tôn_vinh đã tạo nên sức lan_tỏa của phong_trào thi_đua yêu nước của ngành thể_hiệ

In [ ]:
total_score = 0
for example in train_dataset.examples:
    inp = ' '.join(example.src)
    target = ' '.join(example.trg)
    output, bleu_score = eval_instance(model, inp, target)
    total_score += bleu_score

total_score = total_score/len(train_dataset.examples)
print(total_score)

/usr/local/lib/python3.6/dist-packages/nltk/translate/bleu_score.py:490: UserWarning: 
Corpus/Sentence contains 0 counts of 2-gram overlaps.
BLEU scores might be undesirable; use SmoothingFunction().
  warnings.warn(_msg)


0.5762710254868315


In [8]:

for example in np.random.choice(train_dataset.examples, 10, replace=False):
    inp = ' '.join(example.src)
    target = ' '.join(example.trg)
    output, bleu_score = eval_instance(model, inp, target)
    print()
    print('> input doc:', inp)
    print('< output doc:', output)
    print('= target doc:', target)
    print('bleu score:',bleu_score)



> input doc: ngày 23 7 hot_girl khá nổi trên mạng xã_hội trung_quốc nhờ vóc_dáng thon gọn mặt đẹp như búp_bê bị dân mạng bóc phốt ảnh đời thực kém xinh thô_kệch trông như hai người khác nhau cô gái này chỉ là một trong số rất nhiều hot_girl hot boy mạng ở đất_nước tỷ dân bất_chấp che đi nhan_sắc thật để sống ảo câu like trên mạng xã_hội những cái tên như quả_tử_tạng hàn_an_nhiễm thất_hạc tấn triết hứa cống nhất đều từng khiến fan hết_hồn ngỡ như người xa_lạ khi vô_tình bị chụp lén ngoài đường hay tắt filter làm_đẹp khi livestream không riêng các ngôi_sao mạng nhiều người bình_thường thích sử_dụng photoshop phần_mềm chụp và chỉnh_sửa ảnh để dễ_dàng có ngoại_hình lung_linh trên mạng cũng vì thích sống ảo hồi tháng 5 vừa_qua hai cô gái trung_quốc bất_ngờ nhận gạch đá khi bị người lạ đăng loạt ảnh trước và sau khi chỉnh_sửa ảnh quá_đà coey một trong hai nữ chính sau đó tỏ ra bức_xúc vì vô_duyên vô_cớ bị chụp lén rồi đăng lên mạng để bôi_nhọ là con_gái ai chẳng muốn xuất_hiện xinh_đẹp tron

In [ ]:
model = Transformer(
    embedding_size=128,
    src_vocab_size=len(src.vocab),
    trg_vocab_size=len(trg.vocab),
    src_pad_idx=src.vocab.stoi["<pad>"],
    num_heads=4,
    num_encoder_layers=1,
    num_decoder_layers=1,
    forward_expansion=2,
    dropout=0.1,
    max_src_len=1000,
    max_trg_len=1000,
).to(device)
model.load_state_dict(torch.load('/content/drive/MyDrive/DS_data/summary_model.pt'))

train(model, train_dataset, num_epochs=100, lr=0.001, batch_size=32)
torch.save(model.state_dict(),'/content/drive/MyDrive/DS_data/summary_model.pt')

[Epoch 0 / 100]
loss 0.8392079089826886, time 147.91050100326538s
[Epoch 1 / 100]
loss 0.834752730693319, time 152.62923860549927s
[Epoch 2 / 100]
loss 0.8341827686481212, time 155.08333110809326s
[Epoch 3 / 100]
loss 0.83371281449879, time 155.93127155303955s
[Epoch 4 / 100]
loss 0.8339902358029478, time 156.318204164505s
[Epoch 5 / 100]
loss 0.8341909221240452, time 156.3774311542511s
[Epoch 6 / 100]
loss 0.8330211280952401, time 156.29991054534912s
[Epoch 7 / 100]
loss 0.8307919447323144, time 156.06491565704346s
[Epoch 8 / 100]
loss 0.8297401245013909, time 155.95300149917603s
[Epoch 9 / 100]
loss 0.8297460160222471, time 155.8369779586792s
[Epoch 10 / 100]
loss 0.8305150458614947, time 155.90201449394226s
[Epoch 11 / 100]
loss 0.829267953718496, time 156.4901168346405s
[Epoch 12 / 100]
loss 0.8286452232509531, time 156.5234100818634s
[Epoch 13 / 100]
loss 0.8281556040552172, time 156.28888607025146s
[Epoch 14 / 100]
loss 0.8285277218954171, time 156.40536284446716s
[Epoch 15 / 100

In [ ]:
model.load_state_dict(torch.load('/content/drive/MyDrive/DS_data/summary_model.pt'))

train(model, train_dataset, num_epochs=100, lr=0.001, batch_size=32)
torch.save(model.state_dict(),'/content/drive/MyDrive/DS_data/summary_model.pt')

[Epoch 0 / 100]
loss 0.7867927290785331, time 155.8425042629242s
[Epoch 1 / 100]
loss 0.7830498375101573, time 156.08319234848022s
[Epoch 2 / 100]
loss 0.7826936193691787, time 156.2766170501709s
[Epoch 3 / 100]
loss 0.7834783133731643, time 156.50839233398438s
[Epoch 4 / 100]
loss 0.783261778900334, time 156.6723828315735s
[Epoch 5 / 100]
loss 0.7824596445406636, time 156.53834509849548s
[Epoch 6 / 100]
loss 0.7816993616143679, time 156.74805212020874s
[Epoch 7 / 100]
loss 0.7809884410391572, time 156.6512496471405s
[Epoch 8 / 100]
loss 0.7785027877251673, time 156.6126537322998s
[Epoch 9 / 100]
loss 0.7789109997027847, time 156.66642045974731s
[Epoch 10 / 100]
loss 0.7825919782968893, time 156.57430863380432s
[Epoch 11 / 100]
loss 0.7773677395877018, time 156.51239228248596s
[Epoch 12 / 100]
loss 0.7770262824774887, time 156.561993598938s
[Epoch 13 / 100]
loss 0.778380115872704, time 156.74389934539795s
[Epoch 14 / 100]
loss 0.7778280688229428, time 156.43460154533386s
[Epoch 15 / 10